In [1]:
import numpy as np
import pandas as pd

import astropy

from astropy.timeseries import TimeSeries
from astropy.table import Table
from astropy import units as u

import plotly.graph_objects as go

from scipy import signal

import lightkurve as lk

/Users/jacquelinemcshan/miniconda3/lib/python3.9/site-packages/lightkurve/config/__init__.py:119: UserWarning: The default Lightkurve cache directory, used by download(), etc., has been moved to /Users/jacquelinemcshan/.lightkurve/cache. Please move all the files in the legacy directory /Users/jacquelinemcshan/.lightkurve-cache to the new location and remove the legacy directory. Refer to https://docs.lightkurve.org/reference/config.html#default-cache-directory-migration for more information.
  warnings.warn(


from senior experience paper: KOI-4813, KOI-0521 ("KIC 8162789" and "KIC 8162790"), KOI-5869, and KOI-2453

In [56]:
search_result_lc = lk.search_lightcurve("KIC 8162790")
lc_collection = search_result_lc[search_result_lc.author == "Kepler"].download_all()
# want short exposure times https://www.ut.edu/uploadedFiles/Academics/Acta_Spartae/AS_0601p1Argentieri.pdf

In [57]:
search_result_lc

SearchResult containing 14 data products.

 #       mission      year author exptime  target_name  distance
                                     s                   arcsec 
--- ----------------- ---- ------ ------- ------------- --------
  0 Kepler Quarter 04 2010 Kepler    1800 kplr008162790      0.0
  1 Kepler Quarter 05 2010 Kepler    1800 kplr008162790      0.0
  2 Kepler Quarter 06 2010 Kepler    1800 kplr008162790      0.0
  3 Kepler Quarter 07 2010 Kepler    1800 kplr008162790      0.0
  4 Kepler Quarter 08 2011 Kepler    1800 kplr008162790      0.0
  5 Kepler Quarter 09 2011 Kepler    1800 kplr008162790      0.0
  6 Kepler Quarter 10 2011 Kepler    1800 kplr008162790      0.0
  7 Kepler Quarter 11 2012 Kepler    1800 kplr008162790      0.0
  8 Kepler Quarter 12 2012 Kepler    1800 kplr008162790      0.0
  9 Kepler Quarter 13 2012 Kepler    1800 kplr008162790      0.0
 10 Kepler Quarter 14 2012 Kepler    1800 kplr008162790      0.0
 11 Kepler Quarter 15 2013 Kepler    1800 kplr008162790      0.0
 12 Kepler Quarter 16 2013 Kepler    1800 kplr008162790      0.0
 13 Kepler Quarter 17 2013 Kepler    1800 kplr008162790      0.0

According to this [link](https://www.ut.edu/uploadedFiles/Academics/Acta_Spartae/AS_0601p1Argentieri.pdf), we want short exposure times. I am building of these two tutorials: [one](http://docs.lightkurve.org/tutorials/3-science-examples/exoplanets-identifying-transiting-planet-signals.html) and [two](https://docs.lightkurve.org/tutorials/3-science-examples/periodograms-creating-periodograms.html#3.-Using-a-Kepler-Periodogram-to-Identify-a-Significant-Period)

In [58]:
def lightcurve_data(data):
    SAP=[]
    PDCSAP=[]
    norm=[]
    time=[]

    for x in range(0, len(data)-1):
        sap_ind=data[x]['sap_flux'].to_value().tolist()
        pdcsap_ind=data[x]['flux'].to_value().tolist() # source of the flux in the table is PDCSAP FLUX
        norm_ind=data[x].normalize()['flux'].to_value().tolist()
        time_ind=data[x]['time'].to_value('bkjd').tolist()

        SAP.append(sap_ind)
        PDCSAP.append(pdcsap_ind)
        norm.append(norm_ind)
        time.append(time_ind)
    
    stitched=lc_collection.stitch().flatten(window_length=901).remove_outliers()
    fully_norm_flux=stitched['flux'].to_value().tolist() 
    full_time=stitched['time'].to_value('bkjd').tolist()
    return(PDCSAP, SAP, norm, time, fully_norm_flux, full_time, stitched) 


Simple Aperture Photometry = SAP

Pre-search Data Conditioning SAP flux = PDCSAP

More info can be found [here](https://heasarc.gsfc.nasa.gov/docs/tess/LightCurveFile-Object-Tutorial.html)

In [59]:
test1=lightcurve_data(lc_collection)

In [60]:
test1[5]

[352.39716344598855,
 352.43802941675676,
 352.45846240255196,
 352.4788953884563,
 352.49932837471715,
 352.5197613610944,
 352.5401942476965,
 352.5606273346566,
 352.5810603218488,
 352.60149320914934,
 352.62192629680794,
 352.6423592845822,
 352.6627922726984,
 352.68322526093834,
 352.7036582495275,
 352.7240912382258,
 352.74452422728064,
 352.7649572165683,
 352.7853902059651,
 352.80582309571764,
 352.82625618570455,
 352.84668917579984,
 352.8671220662509,
 352.8875551569363,
 352.9079881478465,
 352.9284210388796,
 352.9488541302635,
 352.9692871218722,
 353.01015300580184,
 353.0305860981098,
 353.05101909065706,
 353.0714519834364,
 353.09188507632643,
 353.1123180696886,
 353.1327509631665,
 353.1531840568714,
 353.17361705081566,
 353.194049944992,
 353.2144830393954,
 353.2349160340382,
 353.2553489290294,
 353.27578192413057,
 353.2962150194726,
 353.3166479150459,
 353.33708091096196,
 353.3575139070017,
 353.3779469033907,
 353.3983798998888,
 353.41881299674424,
 35

In [61]:
len(test1)

7

In [62]:
def lightcurve_traces(data):
    upper_range=len(data)-1

    data2plot=lightcurve_data(data)

    SAP_traces={}
    PDCSAP_traces={}
    norm_traces={}
    
    fully_norm_flux_trace=go.Scattergl(x=data2plot[5], y=data2plot[4])

    for x in range(0, upper_range):
        SAP_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[1][x])
        PDCSAP_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[0][x])
        norm_traces['SAP_trace_' + str(x)]=go.Scattergl(x=data2plot[3][x], name=f"Quarter {lc_collection[x].quarter}", y=data2plot[2][x])
    return(PDCSAP_traces, SAP_traces, norm_traces, fully_norm_flux_trace)


In [63]:
test2=lightcurve_traces(lc_collection)

In [64]:
len(test2[0])

13

In [67]:
def lightcurve_plot(data):
    
    traces2plot=lightcurve_traces(data)

    flux_unit=data[0]['flux'].unit.to_string()
    time_unit=data[0]['time'].format

    lc_name=data[0].meta['OBJECT']

    t_ini_limit=float(data[0].meta['TSTART'])
    t_fin_limit=float(data[len(data)-1].meta['TSTOP'])

    PDCSAP_fig_data, SAP_fig_data=list(traces2plot[0].values()), list(traces2plot[1].values())
    norm_fig_data, fully_norm_flux_fig_data=list(traces2plot[2].values()),traces2plot[3]
    
    layout=go.Layout(xaxis=dict(range=[t_ini_limit-20, t_fin_limit+20], autorange=False, zeroline=False),
                  hovermode=False)
    
    PDCSAP_fig, SAP_fig=go.Figure(PDCSAP_fig_data, layout), go.Figure(SAP_fig_data, layout)
    norm_fig, fully_norm_flux_fig=go.Figure(norm_fig_data, layout), go.Figure(fully_norm_flux_fig_data, layout)
    
    PDCSAP_fig.update_layout(title={
        'text': f"{lc_name}'s PDCSAP Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"PDCSAP Flux [{flux_unit}]",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    SAP_fig.update_layout(title={
        'text': f"{lc_name}'s SAP Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"PDCSAP Flux [{flux_unit}]",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    norm_fig.update_layout(title={
        'text': f"{lc_name}'s Normalized Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"Normalized Flux",
                              xaxis_title=f"Days [{time_unit}]", legend_title="Observation Quarters")
    
    fully_norm_flux_fig.update_layout(title={
       ' text': f"{lc_name}'s Normalized and Flattened Lightcurve",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'}, yaxis_title=f"Normalized Flux",
                              xaxis_title=f"Days [{time_unit}]")
    
    return(PDCSAP_fig, SAP_fig, norm_fig, fully_norm_flux_fig)

In [68]:
test3=lightcurve_plot(lc_collection)

In [75]:
test3[0].show()

In [71]:
test3[2].show()

In [72]:
period = np.linspace(1, 40, 25000)
bls = test1[6].to_periodogram(method='bls', period=period, frequency_factor=500)

In [27]:
planet_b_period = bls.period_at_max_power
planet_b_t0 = bls.transit_time_at_max_power
planet_b_dur = bls.duration_at_max_power

In [73]:
folded_lc=test1[6].fold(period=planet_b_period*2, epoch_time=planet_b_t0)
folded_lc_df=folded_lc.to_pandas().reset_index() 
folded_lc_df

time      flux  flux_err                 time_original  quality  \
0     -13.567828  0.999332  0.000397 2012-03-25 12:25:43.578480044        0   
1     -13.567732  1.000514  0.000403 2010-05-17 02:59:44.960561106        0   
2     -13.567286  1.000268  0.000407 2011-05-04 21:21:10.335696009        0   
3     -13.567275  1.000155  0.000402 2013-02-14 03:31:51.461780593        0   
4     -13.567099  1.000401  0.000525 2010-10-26 22:33:19.702891102   393216   
...          ...       ...       ...                           ...      ...   
54881  13.566786  0.999684  0.000404 2010-04-19 23:42:33.948759986        0   
54882  13.567212  0.998964  0.000401 2012-01-31 05:53:51.016017054     8192   
54883  13.567277  1.000048  0.000408 2011-04-07 18:04:03.157654395     8192   
54884  13.567293  0.999553  0.000399 2012-02-27 09:09:24.719368285        0   
54885  13.567672  0.999708  0.000527 2012-01-04 02:39:04.049562165        0   

       timecorr  centroid_col  centroid_row  cadenceno      sap_flux  ...  \
0     -0.001122    777.723585    915.230161      52369  18124.187500  ...   
1      0.001325    946.257615    743.980416      19169  14976.300781  ...   
2      0.000547    946.245161    743.954174      36433  15260.757812  ...   
3     -0.001647    777.717162    915.228411      68305  18200.273438  ...   
4      0.001399    948.986234    748.215857      27137  20779.597656  ...   
...         ...           ...           ...        ...           ...  ...   
54881  0.000213    946.252730    743.968198      17841  15006.583008  ...   
54882 -0.001601    777.715012    915.228573      49713  18400.648438  ...   
54883 -0.000513    946.242507    743.950458      35105  15306.052734  ...   
54884 -0.001623    777.717460    915.226715      51041  18192.017578  ...   
54885 -0.001046    948.970576    748.242963      48385  19931.421875  ...   

       psf_centr1  psf_centr1_err  psf_centr2  psf_centr2_err  mom_centr1  \
0             NaN             NaN         NaN             NaN  777.723585   
1             NaN             NaN         NaN             NaN  946.257615   
2             NaN             NaN         NaN             NaN  946.245161   
3             NaN             NaN         NaN             NaN  777.717162   
4             NaN             NaN         NaN             NaN  948.986234   
...           ...             ...         ...             ...         ...   
54881         NaN             NaN         NaN             NaN  946.252730   
54882         NaN             NaN         NaN             NaN  777.715012   
54883         NaN             NaN         NaN             NaN  946.242507   
54884         NaN             NaN         NaN             NaN  777.717460   
54885         NaN             NaN         NaN             NaN  948.970576   

       mom_centr1_err  mom_centr2  mom_centr2_err  pos_corr1  pos_corr2  
0            0.000138  915.230161        0.000143   0.006041   0.007700  
1            0.000138  743.980416        0.000139  -0.001643   0.009627  
2            0.000140  743.954174        0.000139  -0.000438  -0.002248  
3            0.000139  915.228411        0.000144  -0.001992   0.001168  
4            0.000155  748.215857        0.000138  -0.000717  -0.009774  
...               ...         ...             ...        ...        ...  
54881        0.000141  743.968198        0.000140   0.000819  -0.008550  
54882        0.000138  915.228573        0.000143  -0.003628   0.004013  
54883        0.000140  743.950458        0.000139  -0.002385  -0.006864  
54884        0.000139  915.226715        0.000143   0.002159   0.000229  
54885        0.000158  748.242963        0.000142   0.000159   0.021384  

[54886 rows x 26 columns]

In [ ]:
def lightcurve_bls(data, period):

    initial_data=lightcurve_data(data)
    stitched=initial_data[6]

    bls_period = np.linspace(1, period, 10000)
    bls=stitched.to_periodogram(method='bls', period=bls_period, frequency_factor=500)

    planet_period = bls.period_at_max_power
    planet_t0 = bls.transit_time_at_max_power
    planet_dur = bls.duration_at_max_power

    lc_name=data[0].meta['OBJECT']

    time_unit=bls.to_table()['period'].unit
    bls_df=bls.to_table().to_pandas()

    data_bls=go.Scattergl(x=bls_df['period'], y=bls_df['power'])
    layout_bls=go.Layout(xaxis=dict(range=[bls_df['period'][0], bls_df['period'][len(bls_df)-1]], autorange=False, zeroline=False),
                hovermode=False)
    fig=go.Figure(data=data_bls, layout=layout_bls)
    fig.update_layout(title={
       ' text': f"{lc_name}'s BLS Periodogram",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},yaxis_title=f" BLS Power", xaxis_title=f" days [{time_unit}]")
    
    return(fig, planet_period, planet_t0, planet_dur)


    
    